```
Technische Hochschule Ostwestfalen-Lippe, inIT
Kurs Künstliche Intelligenz (KI), Wintersemester 2020
Malte Schmidt, Arbeitsgruppe Diskrete Systeme
```

# A\*-Suche

In diesem Notebook wird A*-Suche behandelt implementiert. Literaturreferenzen finden Sie in den Lösungshinweisen.

Führen Sie die folgende Codezelle aus. Sie importiert benötigte Bibliotheken und stellt Klassen und Funktionen für eine Problembeschreibung mit einem Zustandsgraphen bereit.

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import math
import random
import heapq

class Problem(object):
    """The abstract class for a formal problem. A new domain subclasses this,
    overriding `actions` and `results`, and perhaps other methods.
    The default heuristic is 0 and the default action cost is 1 for all states.
    When yiou create an instance of a subclass, specify `initial`, and `goal` states 
    (or give an `is_goal` method) and perhaps other keyword args for the subclass."""

    def __init__(self, initial=None, goal=None, **kwds): 
        self.__dict__.update(initial=initial, goal=goal, **kwds) 
        
    def actions(self, state):        raise NotImplementedError
    def result(self, state, action): raise NotImplementedError
    def is_goal(self, state):        return state == self.goal
    def action_cost(self, s, a, s1): return 1
    def h(self, node):               return 0
    
    def __str__(self):
        return '{}({!r}, {!r})'.format(
            type(self).__name__, self.initial, self.goal)
    

class Node:
    "A Node in a search tree."
    def __init__(self, state, parent=None, action=None, path_cost=0):
        self.__dict__.update(state=state, parent=parent, action=action, path_cost=path_cost)

    def __repr__(self): return '<{}>'.format(self.state)
    def __len__(self): return 0 if self.parent is None else (1 + len(self.parent))
    def __lt__(self, other): return self.path_cost < other.path_cost
    
    
failure = Node('failure', path_cost=math.inf) # Indicates an algorithm couldn't find a solution.
cutoff  = Node('cutoff',  path_cost=math.inf) # Indicates iterative deepening search was cut off.
    
    
def expand(problem, node):
    "Expand a node, generating the children nodes."
    s = node.state
    for action in problem.actions(s):
        s1 = problem.result(s, action)
        cost = node.path_cost + problem.action_cost(s, action, s1)
        yield Node(s1, node, action, cost)
        

def path_actions(node):
    "The sequence of actions to get to this node."
    if node.parent is None:
        return []  
    return path_actions(node.parent) + [node.action]


def path_states(node):
    "The sequence of states to get to this node."
    if node in (cutoff, failure, None): 
        return []
    return path_states(node.parent) + [node.state]

failure = Node('failure', path_cost=math.inf) # Indicates an algorithm couldn't find a solution.

Die A*-Suche benötigt eine Warteschlange mit Prioritäten für die Implementation. Diese Warteschlange ist in der folgenden Codezelle implementiert.

In [ ]:
class PriorityQueue:
    """A queue in which the item with minimum f(item) is always popped first."""

    def __init__(self, items=(), key=lambda x: x): 
        self.key = key
        self.items = [] # a heap of (score, item) pairs
        for item in items:
            self.add(item)
         
    def add(self, item):
        """Add item to the queuez."""
        pair = (self.key(item), item)
        heapq.heappush(self.items, pair)

    def pop(self):
        """Pop and return the item with min f(item) value."""
        return heapq.heappop(self.items)[1]
    
    def top(self): return self.items[0][1]

    def __len__(self): return len(self.items)

## Gitterprobleme
Im folgenden werden Probleme betrachtet bei denen durch ein 2D Gitter navigiert werden muss. Einige Zellen sind unpassierbar und es muss ein Weg vom Start zum Ziel gefunden werden. Es kann zu jeder der acht benachbarten Zellen navigiert werden, also ist auch eine diagonale Bewegung möglich. Die eingesetzte Heuristik ist eine gerade Linie vom Start zum Ziel. Ein Zustand ist duch eine Zellposition `(x, y)` beschrieben und Aktionen werden durch ein Tupel `(dx, dy)` beschrieben, in dem die Differenz zur aktuellen Koordinate angegeben wird (entweder 0, 1 oder -1). `(0, -1)` bedeutet, dass die x-Koordinate gleich bleibt und die y-Koordinate um 1 verrringert wird. Es handelt sich also um eine gerade Bewegung nach unten. Die `GridProblem`-Klasse beschreibt ein solches Problem. Die hier verwendete Heurisitk ist die euklidische Distanz zwischen zwei Punkten.

In [ ]:
def g(n): return n.path_cost

def euclidean_distance(A, B):
    "Eucledian distance between two points."
    return sum(abs(a - b)**2 for (a, b) in zip(A, B)) ** 0.5

class GridProblem(Problem):
    """Finding a path on a 2D grid with obstacles. Obstacles are (x, y) cells."""

    def __init__(self, initial=(15, 30), goal=(130, 30), obstacles=(), **kwds):
        Problem.__init__(self, initial=initial, goal=goal, 
                         obstacles=set(obstacles) - {initial, goal}, **kwds)

    directions = [(-1, -1), (0, -1), (1, -1),
                  (-1, 0),           (1,  0),
                  (-1, +1), (0, +1), (1, +1)]
    
    def action_cost(self, s, action, s1): return euclidean_distance(s, s1)
    
    def h(self, node): return euclidean_distance(node.state, self.goal)
                  
    def result(self, state, action): 
        "Both states and actions are represented by (x, y) pairs."
        return action if action not in self.obstacles else state
    
    def actions(self, state):
        """You can move one cell in any of `directions` to a non-obstacle cell."""
        x, y = state
        return {(x + dx, y + dy) for (dx, dy) in self.directions} - self.obstacles

In der folgenden Codezelle werden einige Gitternetzprobleme mit Hindernissen erstellt. 

In [ ]:
# Some grid routing problems

# The following can be used to create obstacles:
    
def random_lines(X=range(15, 130), Y=range(60), N=150, lengths=range(6, 12)):
    """The set of cells in N random lines of the given lengths."""
    result = set()
    for _ in range(N):
        x, y = random.choice(X), random.choice(Y)
        dx, dy = random.choice(((0, 1), (1, 0)))
        result |= line(x, y, dx, dy, random.choice(lengths))
    return result

def line(x, y, dx, dy, length):
    """A line of `length` cells starting at (x, y) and going in (dx, dy) direction."""
    return {(x + i * dx, y + i * dy) for i in range(length)}

random.seed(42) # To make this reproducible

frame = line(-10, 20, 0, 1, 20) | line(150, 20, 0, 1, 20)
cup = line(102, 44, -1, 0, 15) | line(102, 20, -1, 0, 20) | line(102, 44, 0, -1, 24)

d1 = GridProblem(obstacles=random_lines(N=100) | frame)
d2 = GridProblem(obstacles=random_lines(N=150) | frame)
d3 = GridProblem(obstacles=random_lines(N=200) | frame)
d4 = GridProblem(obstacles=random_lines(N=250) | frame)
d5 = GridProblem(obstacles=random_lines(N=300) | frame)
d6 = GridProblem(obstacles=cup | frame)
d7 = GridProblem(obstacles=cup | frame | line(50, 35, 0, -1, 10) | line(60, 37, 0, -1, 17) | line(70, 31, 0, -1, 19))

## A*-Suche
Es soll die A\*-Suche für Gitternetzprobleme an Beispielen untersucht werden. Die Pfadkosten g(n) und die euklidische Distanz als Heurisitk wurden oben definiert.

In [ ]:
def astar_search(problem):
    """Search nodes with minimum f(n) = g(n) + h(n)."""
    h = problem.h  # heuristic
    f = lambda n: g(n) + h(n)
    global reached
    node = Node(problem.initial)
    frontier = PriorityQueue([node], key=f)
    reached = {problem.initial: node}
    while frontier:
        node = frontier.pop()
        if problem.is_goal(node.state):
            return node
        for child in expand(problem, node):
            s = child.state
            if s not in reached or child.path_cost < reached[s].path_cost:
                reached[s] = child
                frontier.add(child)
    return failure

In [ ]:
def plot_grid_problem(grid, solution, reached=(), title='Search', show=True):
    "Use matplotlib to plot the grid, obstacles, solution, and reached."
    reached = list(reached)
    plt.figure(figsize=(16, 10))
    plt.axis('off'); plt.axis('equal')
    plt.scatter(*transpose(grid.obstacles), marker='s', color='darkgrey')
    plt.scatter(*transpose(reached), 1**2, marker='.', c='blue')
    plt.scatter(*transpose(path_states(solution)), marker='s', c='blue')
    plt.scatter(*transpose([grid.initial]), 9**2, marker='D', c='green')
    plt.scatter(*transpose([grid.goal]), 9**2, marker='8', c='red')
    if show: plt.show()
    print('{} {} search: {:.1f} path cost, {:,d} states reached'
          .format(' ' * 10, title, solution.path_cost, len(reached)))
    
def plots(grid, weights=(1.4, 2)): 
    """Plot the results of 4 heuristic search algorithms for this grid."""
    solution = astar_search(grid)
    plot_grid_problem(grid, solution, reached, 'A* search')
    
def transpose(matrix): return list(zip(*matrix))

In [ ]:
plots(d1)

In [ ]:
plots(d2)

In [ ]:
plots(d3)

In [ ]:
plots(d4)

In [ ]:
plots(d5)

In [ ]:
plots(d6)

In [ ]:
plots(d7)

- Entspricht die A\*-Suche ihren Erwartungen oder finden Sie, dass zu viele Punkte analysiert werden müssen? 
- Woran könnte das liegen?
- Haben Sie Verbesserungsvorschläge?